In [1]:
#%load_ext sparksql_magic
from pyspark.sql import SparkSession
from pyspark.sql.functions import expr, col

spark = SparkSession.builder.appName("dim_repo").config("spark.executor.memory", "1g").getOrCreate()

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/03/17 05:20:37 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
25/03/17 05:20:38 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.


In [2]:
for key, value in spark.sparkContext.getConf().getAll():
    if "memory" in key or "executor" in key:
        print(f"{key} = {value}")

spark.executor.memory = 1g
spark.executor.id = driver
spark.executor.extraJavaOptions = -Djava.net.preferIPv6Addresses=false -XX:+IgnoreUnrecognizedVMOptions --add-opens=java.base/java.lang=ALL-UNNAMED --add-opens=java.base/java.lang.invoke=ALL-UNNAMED --add-opens=java.base/java.lang.reflect=ALL-UNNAMED --add-opens=java.base/java.io=ALL-UNNAMED --add-opens=java.base/java.net=ALL-UNNAMED --add-opens=java.base/java.nio=ALL-UNNAMED --add-opens=java.base/java.util=ALL-UNNAMED --add-opens=java.base/java.util.concurrent=ALL-UNNAMED --add-opens=java.base/java.util.concurrent.atomic=ALL-UNNAMED --add-opens=java.base/jdk.internal.ref=ALL-UNNAMED --add-opens=java.base/sun.nio.ch=ALL-UNNAMED --add-opens=java.base/sun.nio.cs=ALL-UNNAMED --add-opens=java.base/sun.security.action=ALL-UNNAMED --add-opens=java.base/sun.util.calendar=ALL-UNNAMED --add-opens=java.security.jgss/sun.security.krb5=ALL-UNNAMED -Djdk.reflect.useDirectMethodHandle=false


In [3]:
df = spark.read.json("/data/*.json.gz")
# Filter for IssuesEvent
df = df.filter(df["type"] == "IssuesEvent")
df = df.select(
    col("actor"),
    col("created_at"),
    col("id").alias("event_id"),
    col("org"),
    col("repo"),
    col("payload.action"),
    col("payload.issue")
)
df.createOrReplaceTempView("df")

25/03/17 05:20:54 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


## For github repo dim data


In [4]:
%%sql
INSERT OVERWRITE TABLE iceberg.dim_repo
SELECT DISTINCT
    CAST(repo.id AS BIGINT) AS id,
    repo.name,
    repo.url
FROM df;

25/03/17 05:20:54 WARN SparkSession: Using an existing Spark session; only runtime SQL configurations will take effect.
                                                                                

++
||
++
++

In [5]:
%%sql 
SELECT
  *
FROM
  iceberg.dim_repo

+-----------+---------------------------------------------------------------+--------------------------------------------------------------------------------------------+
|        id |                                                          name |                                                                                        url |
+-----------+---------------------------------------------------------------+--------------------------------------------------------------------------------------------+
| 862802466 |                                        a-r-r-o-w/finetrainers |                                        https://api.github.com/repos/a-r-r-o-w/finetrainers |
| 493495527 |                                             Mereithhh/vanblog |                                             https://api.github.com/repos/Mereithhh/vanblog |
| 910661922 |                                   stwy0716/yunpan14.github.io |                                   https://api.github.com/repos/stwy0716/yunpan14.github.io |
| 901546068 |                                            nikcladis/yu-gi-oh |                                            https://api.github.com/repos/nikcladis/yu-gi-oh |
| 828722331 |                                       davidkhala/action-tests |                                       https://api.github.com/repos/davidkhala/action-tests |
|  38673738 |                                   goodix/gt9xx_driver_android |                                   https://api.github.com/repos/goodix/gt9xx_driver_android |
| 582137397 |                               ASJordi/website-activity-status |                               https://api.github.com/repos/ASJordi/website-activity-status |
| 588214433 |                       livable-lynchburg/lynchburg-road-issues |                       https://api.github.com/repos/livable-lynchburg/lynchburg-road-issues |
| 504282616 |                      LemmusLemmus/GlosSI-Integration-Playnite |                      https://api.github.com/repos/LemmusLemmus/GlosSI-Integration-Playnite |
| 433677226 |                            MAS-Submod-MoyuTeam/dialogue-packs |                            https://api.github.com/repos/MAS-Submod-MoyuTeam/dialogue-packs |
| 193595523 |                                   tivac/xstate-component-tree |                                   https://api.github.com/repos/tivac/xstate-component-tree |
| 892866928 |                                   jonathanj101/Fax_Service_FE |                                   https://api.github.com/repos/jonathanj101/Fax_Service_FE |
| 734644279 |                                     ToyotaInfoTech/stisr-tcdm |                                     https://api.github.com/repos/ToyotaInfoTech/stisr-tcdm |
| 439665747 |                                      NickvisionApps/Parabolic |                                      https://api.github.com/repos/NickvisionApps/Parabolic |
| 804608716 |                               Neptune-Crypto/neptune-explorer |                               https://api.github.com/repos/Neptune-Crypto/neptune-explorer |
| 302827809 |                                         databendlabs/databend |                                         https://api.github.com/repos/databendlabs/databend |
| 907240594 |                                Ucas-HaoranWei/Slow-Perception |                                https://api.github.com/repos/Ucas-HaoranWei/Slow-Perception |
| 366234394 |                                         gokberkkocak/lofigirl |                                         https://api.github.com/repos/gokberkkocak/lofigirl |
| 830888489 |                              wadakenji/vite-react-boilerplate |                              https://api.github.com/repos/wadakenji/vite-react-boilerplate |
|  93747383 |                                          JannisX11/blockbench |                                          https://api.github.com/repos/JannisX11/blockbench |
| 909934057 | j3-signalroom/ccaf_kickstarter-flight_consolidator_ap

## For github organization data

In [7]:
%%sql
INSERT OVERWRITE TABLE iceberg.dim_org
SELECT DISTINCT
    CAST(org.id AS BIGINT) AS id,
    org.login AS name,
    org.url
FROM df
WHERE org.id IS NOT NULL;

++
||
++
++

In [8]:
%%sql
SELECT
  *
FROM
  iceberg.dim_org

+-----------+---------------------------+-------------------------------------------------------+
|        id |                      name |                                                   url |
+-----------+---------------------------+-------------------------------------------------------+
| 168552997 |            D2R-Reimagined |            https://api.github.com/orgs/D2R-Reimagined |
| 191743538 |             Pedro-Pathing |             https://api.github.com/orgs/Pedro-Pathing |
| 109387420 |              skypilot-org |              https://api.github.com/orgs/skypilot-org |
| 189625046 |          HollowTechnology |          https://api.github.com/orgs/HollowTechnology |
|  96150378 |               AssetRipper |               https://api.github.com/orgs/AssetRipper |
| 103046828 |          travellings-link |          https://api.github.com/orgs/travellings-link |
|    949263 |                   ProgSoc |                   https://api.github.com/orgs/ProgSoc |
| 135339264 |               codestoryai |               https://api.github.com/orgs/codestoryai |
| 102594968 |            Neptune-Crypto |            https://api.github.com/orgs/Neptune-Crypto |
|  76768454 |                 ioccc-src |                 https://api.github.com/orgs/ioccc-src |
|  39381366 |                Chatterino |                https://api.github.com/orgs/Chatterino |
|  33450111 |                 snakemake |                 https://api.github.com/orgs/snakemake |
| 111337716 |                   NatLabs |                   https://api.github.com/orgs/NatLabs |
|   6844498 |                     Azure |                     https://api.github.com/orgs/Azure |
|    995763 |                       ppy |                       https://api.github.com/orgs/ppy |
| 167062371 |               FunAudioLLM |               https://api.github.com/orgs/FunAudioLLM |
|  15366351 |                   geobtaa |                   https://api.github.com/orgs/geobtaa |
|  76995045 |                    vbenjs |                    https://api.github.com/orgs/vbenjs |
| 137588424 |              typst-doc-cn |              https://api.github.com/orgs/typst-doc-cn |
|    426196 |        Unity-Technologies |        https://api.github.com/orgs/Unity-Technologies |
|  19180220 | google-developer-training | https://api.github.com/orgs/google-developer-training |
|    382692 |                 FasterXML |                 https://api.github.com/orgs/FasterXML |
|  19213777 |              xbrowsersync |              https://api.github.com/orgs/xbrowsersync |
|  64161552 |               tenstorrent |               https://api.github.com/orgs/tenstorrent |
| 176628150 |            AlgoArchiveExt |            https://api.github.com/orgs/AlgoArchiveExt |
| 188623155 |               PLSE-Splats |               https://api.github.com/orgs/PLSE-Splats |
| 120078124 |                  ublue-os |                  https://api.github.com/orgs/ublue-os |
| 163827765 |               better-auth |               https://api.github.com/orgs/better-auth |
|   9950313 |                    nodejs |                    https://api.github.com/orgs/nodejs |
| 149747670 |           ClanGenOfficial |           https://api.github.com/orgs/ClanGenOfficial |
| 145161413 |            rollerozxa-org |            https://api.github.com/orgs/rollerozxa-org |
|  18539691 |                   cisagov |                   https://api.github.com/orgs/cisagov |
|   2810941 |       GoogleCloudPlatform |       https://api.github.com/orgs/GoogleCloudPlatform |
| 189301355 |             lazy-eggplant |             https://api.github.com/orgs/lazy-eggplant |
|  60539444 |                   jina-ai |                   https://api.github.com/orgs/jina-ai |
| 182972461 |                 Gazzerapp |                 https://api.github.com/orgs/Gazzerapp |
| 142222059 |                SecOpsNews |                https://api.github.com/orgs/SecOpsNews |
|  15652042 |                  easylist |                  https://api.github.co

## fct_issue_events (github issue events)

In [9]:
%%sql
INSERT OVERWRITE TABLE iceberg.fct_issue_event
SELECT
  -- Primary Key & Event Type
  CAST(event_id AS BIGINT) AS event_id, -- Unique event ID
  action, -- Event type (created, closed, reopened)

  -- Issue Features (ML Inputs)
  issue.title AS issue_title, -- Issue title
  issue.body AS issue_body, -- Issue description
  issue.author_association, -- Creator's association
  issue.state AS issue_state, -- Current state (open, closed)
  issue.state_reason AS issue_state_reason, -- Reason for state change

  -- Issue Creator Struct
  named_struct (
    'id', CAST(issue.user.id AS BIGINT),  -- Ensures consistency
    'login', issue.user.login,
    'url', issue.user.url,
    'is_bot', 
    CASE 
      WHEN issue.user.type != 'Bot' THEN 0 
      ELSE 1 
    END
  ) AS issue_creator,

  -- Other Issue Attributes
  CAST(issue.comments AS BIGINT) AS issue_comment_count, -- Number of comments (could be useful)

  CASE 
    WHEN issue.assignee IS NOT NULL THEN GREATEST(SIZE(issue.assignees), 1) 
    ELSE SIZE(issue.assignees) 
  END AS num_assignees, -- Ensures at least 1 if there’s an assignee

  -- Labels (No changes, still TBD)
  issue.labels, 

  -- Milestone Struct
  CASE 
    WHEN issue.milestone IS NOT NULL THEN named_struct (
      'id', CAST(issue.milestone.id AS BIGINT),
      'title', issue.milestone.title,
      'description', issue.milestone.description,
      'state', issue.milestone.state,
      'closed_issues', CAST(issue.milestone.closed_issues AS BIGINT),
      'open_issues', CAST(issue.milestone.open_issues AS BIGINT),
      'due_on', CAST(issue.milestone.due_on AS TIMESTAMP),
      'created_at', CAST(issue.milestone.created_at AS TIMESTAMP),
      'updated_at', CAST(issue.milestone.updated_at AS TIMESTAMP),
      'closed_at', CAST(issue.milestone.closed_at AS TIMESTAMP)
    ) 
    ELSE NULL 
  END AS milestone,

  -- Timestamps (Time-Based Features)
  CAST(issue.created_at AS TIMESTAMP) AS issue_created_at,
  CAST(issue.closed_at AS TIMESTAMP) AS issue_closed_at,
  CAST(issue.updated_at AS TIMESTAMP) AS issue_updated_at,
  CAST(created_at AS TIMESTAMP) AS event_created_at, -- Timestamp when event occurred

  -- Foreign Keys (For Joins, Placed at the End)
  CAST(issue.id AS BIGINT) AS issue_id, -- FK to Issues
  CAST(actor.id AS BIGINT) AS user_id, -- FK to Users
  CAST(org.id AS BIGINT) AS org_id -- FK to Organizations

FROM df;

++
||
++
++

In [10]:
%%sql
SELECT
  *
FROM
  iceberg.fct_issue_event

+-------------+--------+-------------------------------------------------------------------------------------------------------------------------+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+--------------------+-------------+--------------------+---------------------------------------------------------------------------------------------------------------------------------------------------+---------------------+---------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+---------------------+---------------------+---------------------+---------------------+------------+-----------+-----------+
|    event_id | action |                                                                                                             issue_title |                                                                                                                                                                                                                                                                                                                                                                                                                                                     issue_body | author_association | issue_state | issue_state_reason |                                                                                                                                     issue_creator | issue_comment_count | num_assignees |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        labels |                                                                                                                                                                                                                                                                                                     